# Construct acyclic queries without aggregates

We use the queries of our benchmark datasets: STATS, SNAP, JOB, LSQB, HETIO. With them we already did filter augmentation, which means duplicating the queries with changing some of the filters in the WHERE statement. Now we replace the aggregate in the SELECT part with two random attributes. In in our case we use attributes contained in a join, but it would be possible with any other attribute, too.

In [1]:
import random
import re

In [2]:
def is_number(s):
    try:
        float(s)
        return True
    except ValueError:
        return False

In [3]:
def full_enumeration_queries(query):
    parts = re.split(r'\bWHERE \b', query, flags=re.IGNORECASE)[1].split(" AND ")

    # get the join attributes
    attributes = []
    for p in parts:
        p_split = p.split("=")
        if len(p_split) == 2 and p_split[1].count("'") == 0 and p_split[1].count('"') == 0 and is_number(p_split[1].strip()) == False:
            attributes += p_split
            
    attributes = list(set([s.strip() for s in attributes]))

    # get the 3 queries, with two random attributes in the select (without a MIN)
    query_full1 = "SELECT " + ", ".join(random.sample(attributes, 2)) + " FROM " + re.split(r'\bFROM \b', query, flags=re.IGNORECASE)[1]
    query_full2 = ""
    query_full3 = ""
    if len(attributes) > 2:
        query_full2 = "SELECT " + ", ".join(random.sample(attributes, 2)) + " FROM " + re.split(r'\bFROM \b', query, flags=re.IGNORECASE)[1]
        while query_full1 == query_full2:
            query_full2 = "SELECT " + ", ".join(random.sample(attributes, 2)) + " FROM " + re.split(r'\bFROM \b', query, flags=re.IGNORECASE)[1]
        query_full3 = "SELECT " + ", ".join(random.sample(attributes, 2)) + " FROM " + re.split(r'\bFROM \b', query, flags=re.IGNORECASE)[1]
        while (query_full1 == query_full3 or query_full2 == query_full3):
            query_full3 = "SELECT " + ", ".join(random.sample(attributes, 2)) + " FROM " + re.split(r'\bFROM \b', query, flags=re.IGNORECASE)[1]

    return query_full1, query_full2, query_full3

In [4]:
full_enumeration_queries("SELECT MIN(ph.id) FROM comments as c, postLinks as pl, postHistory as ph, votes as v, posts as p WHERE pl.PostId = p.Id AND c.PostId = p.Id AND v.PostId = p.Id AND ph.PostId = p.Id AND c.Score=0 AND pl.CreationDate>=CAST('2011-03-22 06:18:34' AS TIMESTAMP) AND pl.CreationDate<=CAST('2014-08-22 20:04:25' AS TIMESTAMP)")

("SELECT c.PostId, p.Id FROM comments as c, postLinks as pl, postHistory as ph, votes as v, posts as p WHERE pl.PostId = p.Id AND c.PostId = p.Id AND v.PostId = p.Id AND ph.PostId = p.Id AND c.Score=0 AND pl.CreationDate>=CAST('2011-03-22 06:18:34' AS TIMESTAMP) AND pl.CreationDate<=CAST('2014-08-22 20:04:25' AS TIMESTAMP)",
 "SELECT v.PostId, c.PostId FROM comments as c, postLinks as pl, postHistory as ph, votes as v, posts as p WHERE pl.PostId = p.Id AND c.PostId = p.Id AND v.PostId = p.Id AND ph.PostId = p.Id AND c.Score=0 AND pl.CreationDate>=CAST('2011-03-22 06:18:34' AS TIMESTAMP) AND pl.CreationDate<=CAST('2014-08-22 20:04:25' AS TIMESTAMP)",
 "SELECT ph.PostId, p.Id FROM comments as c, postLinks as pl, postHistory as ph, votes as v, posts as p WHERE pl.PostId = p.Id AND c.PostId = p.Id AND v.PostId = p.Id AND ph.PostId = p.Id AND c.Score=0 AND pl.CreationDate>=CAST('2011-03-22 06:18:34' AS TIMESTAMP) AND pl.CreationDate<=CAST('2014-08-22 20:04:25' AS TIMESTAMP)")

In [4]:
# Define input and output file paths
input_file = 'scala_commands_augment_filter.txt'
output_file = 'scala_commands_augment_full_enum.txt'

# Open input and output files
with open(input_file, 'r') as f_input, open(output_file, 'w') as f_output:

    first = True
    for line in f_input:
        splitted = re.split(r'(?<!\\)"', line)
        
        # Create 3 new queries, which need full enumeration
        query_full1, query_full2, query_full3 = full_enumeration_queries(splitted[1])

        # Write them to a text file
        new_line1 = '\n' + 'run "' + query_full1 + '" "' + splitted[3] + '" "' + splitted[5] + '-full1"'
        new_line2 = '\n' + 'run "' + query_full2 + '" "' + splitted[3] + '" "' + splitted[5] + '-full2"'
        new_line3 = '\n' + 'run "' + query_full3 + '" "' + splitted[3] + '" "' + splitted[5] + '-full3"'

        if first == True:
            new_line1 = 'run "' + query_full1 + '" "' + splitted[3] + '" "' + splitted[5] + '-full1"'
            first = False

        f_output.write(new_line1)
        if not query_full2 == "":
            f_output.write(new_line2)
        if not query_full3 == "":
            f_output.write(new_line3)

# Rewrite the queries

In [2]:
%%bash
pip3 install psycopg2-binary

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.0/3.0 MB 22.9 MB/s eta 0:00:00


In [3]:
import subprocess
import psycopg2
from pathlib import Path
import json

In [7]:
filename = 'scala_commands_augment_full_enum.txt'
REWRITE_JAR = 'rewrite-assembly-0.1.0-SNAPSHOT.jar'

def rewrite(host, database, user, password, query, name, port = 5432):
    rewriteProcess = subprocess.run(['java', '-jar', REWRITE_JAR, query, f'jdbc:postgresql://{host}:{port}/{database}', 
                                     database, user, password, name])
    print(rewriteProcess.returncode)
    if (rewriteProcess.returncode != 0):
        print(f'Error calling {rewriteProcess}')
        return None

with open(filename, 'r') as file:
    for line in file:
        splitted = line.split(' \"')
        query = splitted[1][:-1].replace('\\\\\\\"','"')
        database = splitted[2][:-1].lower()
        if database == "job":
            database = "imdb"
        name = splitted[3].replace("\n", "")[:-1]
        result = rewrite("postgres", database, database, database, query, name)

SLF4J: No SLF4J providers were found.
SLF4J: Defaulting to no-operation (NOP) logger implementation
SLF4J: See https://www.slf4j.org/codes.html#noProviders for further details.


ERROR StatusLogger Log4j2 could not find a logging implementation. Please add log4j-core to the classpath. Using SimpleLogger to log to the console...


org.apache.calcite.jdbc.CalciteSchema$SchemaPlusImpl@22590e3eLogicalProject(ID=[$11], USERID=[$4])
  LogicalJoin(condition=[=($4, $11)], joinType=[inner])
    LogicalJoin(condition=[=($4, $9)], joinType=[inner])
      LogicalFilter(condition=[SEARCH($3, Sarg[[2010-10-01 20:45:26..2014-09-05 12:51:17]])])
        JdbcTableScan(table=[[stats, comments]])
      LogicalFilter(condition=[<=($5, 100)])
        JdbcTableScan(table=[[stats, votes]])
    LogicalFilter(condition=[AND(=($4, 0), <=($2, 2014-09-12 03:25:34))])
      JdbcTableScan(table=[[stats, users]])

attributes: List($0, $1, $2, $3, $4, $5, $6, $7, $8, $9, $10, $11, $12, $13, $14, $15, $16)
aggAttributes: List()
conditions: List(=($4, $9), =($4, $11))
combined equivalence classes: Set(Set($4, $9, $11))
attribute to vertex mapping: HashMap($4 -> $4, $9 -> $4, $11 -> $4)
hyperedges: HashSet(E2($4), E3($4), E1($4))
projectAttributes: Set($11, $4)
joinAttributes: Set($4, $9, $11)
projectJoinAttributes: Set($11, $4, $9)
query has no

SLF4J: No SLF4J providers were found.
SLF4J: Defaulting to no-operation (NOP) logger implementation
SLF4J: See https://www.slf4j.org/codes.html#noProviders for further details.


ERROR StatusLogger Log4j2 could not find a logging implementation. Please add log4j-core to the classpath. Using SimpleLogger to log to the console...


...

ERROR StatusLogger Log4j2 could not find a logging implementation. Please add log4j-core to the classpath. Using SimpleLogger to log to the console...


org.apache.calcite.jdbc.CalciteSchema$SchemaPlusImpl@22590e3eLogicalProject(NID=[$0], SID=[$2])
  LogicalJoin(condition=[=($18, $20)], joinType=[inner])
    LogicalJoin(condition=[=($16, $19)], joinType=[inner])
      LogicalJoin(condition=[=($15, $16)], joinType=[inner])
        LogicalJoin(condition=[=($12, $14)], joinType=[inner])
          LogicalJoin(condition=[=($11, $12)], joinType=[inner])
            LogicalJoin(condition=[=($8, $10)], joinType=[inner])
              LogicalJoin(condition=[=($6, $8)], joinType=[inner])
                LogicalJoin(condition=[=($4, $7)], joinType=[inner])
                  LogicalJoin(condition=[=($2, $4)], joinType=[inner])
                    LogicalJoin(condition=[=($0, $3)], joinType=[inner])
                      JdbcTableScan(table=[[hetio, symptom]])
                      JdbcTableScan(table=[[hetio, presents]])
                    JdbcTableScan(table=[[hetio, disease]])
                  JdbcTableScan(table=[[hetio, treats]])
           

SLF4J: No SLF4J providers were found.
SLF4J: Defaulting to no-operation (NOP) logger implementation
SLF4J: See https://www.slf4j.org/codes.html#noProviders for further details.


ERROR StatusLogger Log4j2 could not find a logging implementation. Please add log4j-core to the classpath. Using SimpleLogger to log to the console...


org.apache.calcite.jdbc.CalciteSchema$SchemaPlusImpl@22590e3eLogicalProject(TID=[$7], NID=[$16])
  LogicalJoin(condition=[=($18, $20)], joinType=[inner])
    LogicalJoin(condition=[=($16, $19)], joinType=[inner])
      LogicalJoin(condition=[=($15, $16)], joinType=[inner])
        LogicalJoin(condition=[=($12, $14)], joinType=[inner])
          LogicalJoin(condition=[=($11, $12)], joinType=[inner])
            LogicalJoin(condition=[=($8, $10)], joinType=[inner])
              LogicalJoin(condition=[=($6, $8)], joinType=[inner])
                LogicalJoin(condition=[=($4, $7)], joinType=[inner])
                  LogicalJoin(condition=[=($2, $4)], joinType=[inner])
                    LogicalJoin(condition=[=($0, $3)], joinType=[inner])
                      JdbcTableScan(table=[[hetio, symptom]])
                      JdbcTableScan(table=[[hetio, presents]])
                    JdbcTableScan(table=[[hetio, disease]])
                  JdbcTableScan(table=[[hetio, treats]])
          

In [4]:
filename = 'scala_commands_augment_full_enum_some_new.txt'
REWRITE_JAR = 'rewrite-assembly-0.1.0-SNAPSHOT.jar'

def rewrite(host, database, user, password, query, name, port = 5432):
    rewriteProcess = subprocess.run(['java', '-jar', REWRITE_JAR, query, f'jdbc:postgresql://{host}:{port}/{database}', 
                                     database, user, password, name])
    print(rewriteProcess.returncode)
    if (rewriteProcess.returncode != 0):
        print(f'Error calling {rewriteProcess}')
        return None

with open(filename, 'r') as file:
    for line in file:
        splitted = line.split(' \"')
        query = splitted[1][:-1].replace('\\\\\\\"','"')
        database = splitted[2][:-1].lower()
        if database == "job":
            database = "imdb"
        name = splitted[3].replace("\n", "")[:-1]
        result = rewrite("postgres", database, database, database, query, name)

SLF4J: No SLF4J providers were found.
SLF4J: Defaulting to no-operation (NOP) logger implementation
SLF4J: See https://www.slf4j.org/codes.html#noProviders for further details.


ERROR StatusLogger Log4j2 could not find a logging implementation. Please add log4j-core to the classpath. Using SimpleLogger to log to the console...


org.apache.calcite.jdbc.CalciteSchema$SchemaPlusImpl@22590e3eLogicalProject(FROMNODE=[$4], FROMNODE0=[$6])
  LogicalJoin(condition=[=($5, $6)], joinType=[inner])
    LogicalJoin(condition=[=($3, $4)], joinType=[inner])
      LogicalJoin(condition=[=($1, $2)], joinType=[inner])
        JdbcTableScan(table=[[snap, dblp]])
        JdbcTableScan(table=[[snap, dblp]])
      JdbcTableScan(table=[[snap, dblp]])
    JdbcTableScan(table=[[snap, dblp]])

attributes: List($0, $1, $2, $3, $4, $5, $6, $7)
aggAttributes: List()
conditions: List(=($1, $2), =($3, $4), =($5, $6))
combined equivalence classes: Set(Set($1, $2), Set($3, $4), Set($5, $6))
attribute to vertex mapping: HashMap($1 -> $1, $2 -> $1, $3 -> $3, $4 -> $3, $5 -> $5, $6 -> $5)
hyperedges: HashSet(E3($3, $5), E1($1), E2($1, $3), E4($5))
projectAttributes: Set($4, $6)
joinAttributes: HashSet($5, $1, $6, $2, $3, $4)
projectJoinAttributes: HashSet($5, $1, $6, $2, $3, $4)
query has no attributes
depth: 2
container counts: List(1, 1, 1, 1

SLF4J: No SLF4J providers were found.
SLF4J: Defaulting to no-operation (NOP) logger implementation
SLF4J: See https://www.slf4j.org/codes.html#noProviders for further details.


ERROR StatusLogger Log4j2 could not find a logging implementation. Please add log4j-core to the classpath. Using SimpleLogger to log to the console...


...

ERROR StatusLogger Log4j2 could not find a logging implementation. Please add log4j-core to the classpath. Using SimpleLogger to log to the console...


org.apache.calcite.jdbc.CalciteSchema$SchemaPlusImpl@22590e3eLogicalProject(NID=[$0], SID=[$2])
  LogicalJoin(condition=[=($18, $20)], joinType=[inner])
    LogicalJoin(condition=[=($16, $19)], joinType=[inner])
      LogicalJoin(condition=[=($15, $16)], joinType=[inner])
        LogicalJoin(condition=[=($12, $14)], joinType=[inner])
          LogicalJoin(condition=[=($11, $12)], joinType=[inner])
            LogicalJoin(condition=[=($8, $10)], joinType=[inner])
              LogicalJoin(condition=[=($6, $8)], joinType=[inner])
                LogicalJoin(condition=[=($4, $7)], joinType=[inner])
                  LogicalJoin(condition=[=($2, $4)], joinType=[inner])
                    LogicalJoin(condition=[=($0, $3)], joinType=[inner])
                      JdbcTableScan(table=[[hetio, symptom]])
                      JdbcTableScan(table=[[hetio, presents]])
                    JdbcTableScan(table=[[hetio, disease]])
                  JdbcTableScan(table=[[hetio, treats]])
           

SLF4J: No SLF4J providers were found.
SLF4J: Defaulting to no-operation (NOP) logger implementation
SLF4J: See https://www.slf4j.org/codes.html#noProviders for further details.


ERROR StatusLogger Log4j2 could not find a logging implementation. Please add log4j-core to the classpath. Using SimpleLogger to log to the console...


org.apache.calcite.jdbc.CalciteSchema$SchemaPlusImpl@22590e3eLogicalProject(TID=[$7], NID=[$16])
  LogicalJoin(condition=[=($18, $20)], joinType=[inner])
    LogicalJoin(condition=[=($16, $19)], joinType=[inner])
      LogicalJoin(condition=[=($15, $16)], joinType=[inner])
        LogicalJoin(condition=[=($12, $14)], joinType=[inner])
          LogicalJoin(condition=[=($11, $12)], joinType=[inner])
            LogicalJoin(condition=[=($8, $10)], joinType=[inner])
              LogicalJoin(condition=[=($6, $8)], joinType=[inner])
                LogicalJoin(condition=[=($4, $7)], joinType=[inner])
                  LogicalJoin(condition=[=($2, $4)], joinType=[inner])
                    LogicalJoin(condition=[=($0, $3)], joinType=[inner])
                      JdbcTableScan(table=[[hetio, symptom]])
                      JdbcTableScan(table=[[hetio, presents]])
                    JdbcTableScan(table=[[hetio, disease]])
                  JdbcTableScan(table=[[hetio, treats]])
          